# L3 Analyse Numérique – TP2

[Dequay A](mailto:antoine.dequay@ens-rennes.fr) &
[Le Barbenchon P](mailto:pierre.le-barbenchon@ens-rennes.fr). TP ENS Rennes

[Boutin B](mailto:benjamin.boutin@univ-rennes1.fr). Cours et TP Université de Rennes 1 - UFR Mathématiques  

Ce TP a pour objet la résolution de systèmes linéaires.

- Exercice 1. *Conditionnement* d'une matrice de taille fixée dépendant d'un paramètre.
- Exercice 2. Résolution d'un problème d'élasticité par une méthode de différences finies.
- Exercice 3. Approche optimisée par stockage creux 'sparse'

## Exercice 1. Conditionnement d'une matrice

Nous importons avant tout quelques librairies qui seront utiles.

In [1]:
from math import *
import numpy as np
import matplotlib.pyplot as plt

In [2]:
# Au besoin (?)
# import sys
# !{sys.executable} -m pip install scipy

Étant donnée une matrice inversible $M\in\mathsf{GL}_n(\mathbb{R})$ et une donnée $b\in\mathbb{R}^n$, la résolution du système linéaire $Mx=b$ peut s'avérer particulièrement sensible aux imprécisions sur la donnée $b$, *ceci même pour des calculs menés en arithmétique exacte*. Un résultat du cours concerne l'erreur relative commise sur la solution $x$ qui peut être contrôlée à l'aide du conditionnement de $M$ défini comme étant la quantité:  

$$\mathsf{cond}\,M:= \|M\|\,\|M^{-1}\|.$$

En l'occurence, si $Mx=b$ et $My=b+\delta b$ avec $x\neq 0$, alors l'inégalité suivante est satisfaite:  

$$
\dfrac{\|y-x\|}{\|x\|}\leq \mathsf{cond}\, M \dfrac{\|\delta b\|}{\|b\|}.
\tag{Err relat.}
$$


En Python, le conditionnement s'obtient à l'aide de la commande [`numpy.linalg.cond`](https://numpy.org/doc/stable/reference/generated/numpy.linalg.cond.html).

Dans cet exercice, on s'intéressera à la matrice $M_\alpha$ suivante, dépendant d'un paramètre réel $\alpha$:
$$
M_\alpha=
\begin{pmatrix}
 1+\alpha&1&2\\
 3&1&\alpha\\
 1&2\alpha&1
\end{pmatrix}.
$$
**Attention.** Cette matrice n'est pas inversible pour toutes les valeurs du paramètre $\alpha$.  
L'espace vectoriel $\mathbb{R}^3$ est muni de la norme euclidienne usuelle notée $\|\cdot\|$, qui s'obtient en Python par la fonction [`numpy.linalg.norm`](https://numpy.org/doc/stable/reference/generated/numpy.linalg.norm.html#numpy.linalg.norm). Les erreurs seront calculés dans cette norme ainsi que le conditionnement de la matrice.

### Question 1)

Programmer une fonction Python `def Malpha(alpha):` qui renvoie un `numpy.array` de `float` représentant la matrice $M_\alpha$.  
Calculer ensuite $M_2$ et vérifier qu'elle n'est pas inversible.

### Question 2)

Soit $\alpha=2.01$ pour lequel la matrice $M_\alpha$ est inversible.  
Étant donné $x=(1,1,1)^T$, on considère le second membre $b=M_\alpha x$.

**a)** Calculer $y\in\mathbb{R}^3$ la solution du système linéaire $M_\alpha y=b+\delta b$ où $\delta b\in\mathbb{R}^3$ est une perturbation vectorielle obtenue par une réalisation d'un aléa de petite amplitude `0.01*np.random.rand(3,1)`.

**b)** Calculer alors numériquement l'erreur relative sur la solution
$$
\dfrac{\|y-x\|}{\|x\|},
$$
puis vérifier numériquement que l'inégalité (Err relat.) est bien réalisée.

### Question 3) 

Reprendre la question précédente de façon à traiter un grand nombre de valeurs de $\alpha\in[-5,5]$ (choisies aléatoirement) et des données $x$ et $\delta b$ aléatoires pour chaque $\alpha$. L'objectif est de visualiser graphiquement l'inégalité (Err relat.). On pourra considérer la quantité: 
$$
\tau = \left(\dfrac{\|y-x\|}{\|x\|}\right)\left(\dfrac{\|\delta b\|}{\|b\|}\right)^{-1},
$$  
et représenter séparément en fonction de $\alpha$ les quantités $\tau$, $\det(M_\alpha)$ et $\dfrac{\tau}{\mathsf{cond}\, M_\alpha}$.

Le code suivant peut vous servir de base.
```python
n = 50

fig, (ax1, ax2, ax3) = plt.subplots(3,figsize=(10,10))
Lalpha = np.zeros(n)
Lx, Ly, Lz = np.zeros(n), np.zeros(n), np.zeros(n)

for i in range(n):
    alpha = np.random.rand() * 10 - 5
    
    x = alpha
    y = alpha**2
    z = alpha**3

    Lalpha[i] = alpha
    Lx[i] = x
    Ly[i] = y
    Lz[i] = z
    
ax1.plot(Lalpha,Lx,'.')
ax2.plot(Lalpha,Ly,'.')
ax3.plot(Lalpha,Lz,'.')
    
plt.show()
```

## Exercice 2. Problème d'élasticité

On souhaite déterminer une approximation de la solution $u\in\mathcal{C}^2(]0,1[)\cap\mathcal{C}^0([0,1])$ du **problème aux limites** suivant:  

$$
\begin{cases}
\dfrac{d}{dx}\left(a(x)\dfrac{du}{dx}\right) = f(x),& 0<x<1,\\
u(0)=u(1)=0. & 
\end{cases}
$$

La quantité $u(x)$ représente le déplacement vertical d'une corde élastique pesante à l'équilibre dont la position en l'absence de forces extérieures (i.e. lorsque $f\equiv 0$) serait horizontale ($u\equiv 0$). Son élasticité en tout point d'abscisse $x\in[0,1]$ est donnée par le coefficient $a(x)>0$. La corde est fixée aux deux points extrémaux de coordonnées $(0,0)$ et $(1,0)$ et est soumise à la charge linéique $f$ qui en modifie la géométrie par l'effet de la gravité.

Nous décrivons une stratégie de résolution numérique approchée qui s'appuie sur **une approximation en dimension finie du problème**.  

Pour ce faire, considérons un entier naturel non nul $n\in\mathbb{N}$ à partir duquel est définie une discrétisation de l'intervalle d'espace $x\in[0,1]$: notons $h=(n+1)^{-1}$ le pas de discrétisation et pour tout entier $i$, posons $x_i=ih$ et $x_{i+1/2}=(i+1/2)h$.  

L'inconnue du problème à résoudre est alors le vecteur $U=(u_1,\ldots,u_n)^T\in\mathbb{R}^n$, solution des équations aux différences finies suivantes:  

$$
\begin{aligned}
&\dfrac{1}{h}\left(a(x_{i+1/2})\dfrac{u_{i+1}-u_{i}}{h}-a(x_{i-1/2})\dfrac{u_{i}-u_{i-1}}{h}\right) = f(x_i),\quad 1\leq i \leq n,\\
&u_0 = u_{n+1} = 0.
\end{aligned}
\tag{Pb}
$$

On admettra que la solution $U$ de ce problème discret approche bien celle du problème continu $u$ au sens par exemple où la quantité  

$$\max_{1\leq i \leq n} \vert u_i-u(x_i)\vert$$

converge vers $0$ lorsque la dimension $n$ tend vers l'infini.

### Question 1)

Identifier *sur le papier* avec soin une matrice $A\in\mathsf{M}_n(\mathbb{R})$ et un vecteur $F\in\mathbb{R}^n$ permettant de réécrire le problème (Pb) d'inconnue $U\in\mathbb{R}^n$ sous la forme d'un système linéaire $AU=F$.  

### Question 2)

Programmer la construction de la matrice $A$ et du second membre $F$, à travers une fonction dont la syntaxe sera la suivante, à compléter:
```python
def construction(n,a,f):
	# n entier, a et f le nom des fonctions concernees
	h = 1./(n+1)
	x = np.arange(0,n+2)*h
    vec = a(x[:-1]+0.5*h)
    ...            # Astuce: utiliser l'instruction np.diag vue au TP1
    return A,F
```

### Question 3)

Vérifier que, dans le cas des fonctions $a$ et $f$ constantes égales à 1:
$$
\begin{aligned}
a(x) &= 1,\\
f(x) &= 1, 
\end{aligned}
$$
et pour une valeur de $n$ à votre convenance, le vecteur suivant
$$
U=\left(\dfrac{x_i(x_i-1)}{2}\right)_{1\leq i \leq n}
$$
est bien solution du problème (Pb) à l'erreur machine près.  
On pourra faire usage de la commande `np.linalg.solve` documentée dans l'aide.

### Question 4)

Désormais, les fonctions $a$ et $f$ sont choisies selon les paramètres suivants:  

$$
\begin{aligned}
a(x) &= 1 -0.95\mathrm{e}^{-500(x-0.25)^2},\\
f(x) &= 0.1 + 0.75\mathrm{e}^{-1000(x-\xi_1)^2} + 2\mathrm{e}^{-1000(x-\xi_2)^2}.
\end{aligned}
$$

Dans la fonction $f$ ainsi définie, le terme constant peut s'interpréter comme la contribution de la masse propre de la corde, tandis que les deux termes exponentiellement localisés modélisent deux masses suspendues, placées au voisinage des points d'abscisses respectives $\xi_1=0.2$ et $\xi_2=0.8$.

```python
def a(x):
    return 1 - 0.95*np.exp(-500*(x-0.25)**2)

xi1 = 0.2
xi2 = 0.8
def f(x):
    return 0.1 + 0.75*np.exp(-1000*(x-xi1)**2) + 2*np.exp(-1000*(x-xi2)**2)

fig, ax1 = plt.subplots()
ax2 = ax1.twinx()
x = np.linspace(0, 1, 200)
ax1.plot(x, a(x), 'g-')
ax2.plot(x, f(x), 'b-')

ax1.set_xlabel('position')
ax1.set_ylabel('elasticité', color='g')
ax2.set_ylabel('chargement', color='b')
plt.show()
```

### Question 4a)

Calculer la matrice $A$ qui intervient pour une discrétisation de $n=5$ points intérieurs et vérifier numériquement que $A$ est alors bien symétrique, définie et négative. Si ce n'est pas le cas, c'est qu'il y a une erreur dans votre fonction `construction` à la question 2 !

### Question 4b)

Résoudre le problème (Pb) avec les nouvelles données $a$ et $f$ et représenter la corde pour différentes valeurs de $n$. Si possible, on ajoutera dans la représentation graphique les conditions de bord $u(0)=0=u(1)$ qui ont été initialement écartées du vecteur $U$ (utiliser pour cela par exemple `np.concatenate`).

## Exercice 3

Cet exercice fait suite au précédent.

Pour de grandes valeurs de $n$, le temps de calcul nécessaire pour construire la matrice $A$ puis pour résoudre le système linéaire $AU=F$ devient important. Nous allons dans la suite utiliser une stratégie de résolution adaptée à la structure particulière de la matrice $A$. De nombreuses stratégies sont possibles mais un gain d'efficacité conséquent s'obtient en mettant à profit la **structure creuse** de $A$, c'est à dire en adaptant le stockage des variables et les algorithmes de résolution de façon à ne pas tenir compte des très nombreux éléments nuls de $A$, ici localisés "loin" de la diagonale. La librairie `scipy` fournit différents stockages creux et des algorithmes d'algèbre linéaires adaptés. 

### Question 1)

Tester les trois cellules de code suivantes et commentez.

In [ ]:
import numpy as np
import scipy.sparse as sp
from scipy.sparse.linalg import spsolve

print(np.diag(np.arange(5.),1))
print(sp.diags(np.arange(5),1))

[[0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 2. 0. 0.]
 [0. 0. 0. 0. 3. 0.]
 [0. 0. 0. 0. 0. 4.]
 [0. 0. 0. 0. 0. 0.]]
  (1, 2)	1.0
  (2, 3)	2.0
  (3, 4)	3.0
  (4, 5)	4.0


In [ ]:
%%time
n = 2000
A = np.eye(n,n)
x = np.ones(n)
y = np.linalg.solve(A,x)

In [ ]:
%%time
n = 200000
A = sp.eye(n,n,format='csr')
x = np.ones((n,1))
y = spsolve(A,x)

Dans la suite, nous utiliserons systématiquement ce stockage creux. La fonction `construction` a été réécrite de façon adaptée en une nouvelle fonction `constructionSP` définie par:
```python
def constructionSP(n,a,f):
    h = 1./(n+1)
    x = np.arange(0,n+2)*h
    vec = a((0.5+np.arange(n+1))*h)
    A = (sp.diags(vec[1:-1],1,format='csr')+sp.diags(vec[1:-1],-1,format='csr')-sp.diags(vec[:-1]+vec[1:],format='csr'))/h**2
    F = f(x[1:-1])
    return A,F
```

### Question 2)

Revenons à notre problème d'élasticité (Pb). La seconde charge est supposée fixée à la position $\xi_2=0.8$. On souhaite maintenant optimiser la position $\xi_1$ de la première masse de façon à maximiser l'amplitude de la corde, autrement dit, à minimiser la quantité négative $\min_{x\in[0,1]} u(x)$.  
Proposer et mettre en œuvre un procédé numérique de votre choix qui aborde ce problème.  
On pourra tester et décrypter au préalable la commande suivante:
```python
test = (np.linspace(0,10,11)-5.)**2
print(test)
np.where(test == np.min(test))[0][0]
```

### Question 3)

Reprendre la question précédente, avec cette fois-ci les deux positions $\xi_1\in[0,1]$ et $\xi_2\in[0,1]$ à optimiser.  

On pourra jeter un œil aux exemples d'utilisation de la fonction [`matplotlib.contour`](https://matplotlib.org/stable/gallery/images_contours_and_fields/contour_demo.html) et utiliser la commande `numpy.meshgrid`.